<a href="https://colab.research.google.com/github/marcelo-guimaraes/Data-Science/blob/master/Detroit_Blight_Violation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Understanding and Predicting Property Maintenance Fines

This notebook is based on a data challenge from the Michigan Data Science Team ([MDST](http://midas.umich.edu/mdst/)). 

The Michigan Data Science Team ([MDST](http://midas.umich.edu/mdst/)) and the Michigan Student Symposium for Interdisciplinary Statistical Sciences ([MSSISS](https://sites.lsa.umich.edu/mssiss/)) have partnered with the City of Detroit to help solve one of the most pressing problems facing Detroit - blight. [Blight violations](http://www.detroitmi.gov/How-Do-I/Report/Blight-Complaint-FAQs) are issued by the city to individuals who allow their properties to remain in a deteriorated condition. Every year, the city of Detroit issues millions of dollars in fines to residents and every year, many of these fines remain unpaid. Enforcing unpaid blight fines is a costly and tedious process, so the city wants to know: how can we increase blight ticket compliance?

The first step in answering this question is understanding when and why a resident might fail to comply with a blight ticket. This is where predictive modeling comes in. The task is to predict whether a given blight ticket will be paid on time.


___


 The target variable is compliance, which is True if the ticket was paid early, on time, or within one month of the hearing data and False if the ticket was paid after the hearing date or not at all. Compliance, as well as a handful of other variables that will not be available at test-time, are only included in train.csv.

In [49]:
!pip install scikit-optimize

### Import Libraries and Data

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings("ignore")

import folium 

from sklearn.neural_network import MLPClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import RandomForestClassifier

from skopt import gp_minimize

import imblearn
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import train_test_split

from sklearn.metrics import recall_score, accuracy_score, f1_score, roc_auc_score
from sklearn.model_selection import cross_val_score

%matplotlib inline

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [3]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


### Exploring the Datasets

In [4]:
df_train = pd.read_csv('/content/drive/My Drive/train.csv', encoding = "ISO-8859-1")
df_test = pd.read_csv('/content/drive/My Drive/test.csv', encoding = "ISO-8859-1")
address = pd.read_csv('/content/drive/My Drive/addresses.csv', encoding = "ISO-8859-1")
latlons = pd.read_csv('/content/drive/My Drive/latlons.csv', encoding = "ISO-8859-1")

In [5]:
print("Train Data Shape: {}\n".format(df_train.shape),
      "Test Data Shape: {}".format(df_test.shape))
df_train.head(3)

Train Data Shape: (250306, 34)
 Test Data Shape: (61001, 27)


ticket_id  ... compliance
0      22056  ...        0.0
1      27586  ...        1.0
2      22062  ...        NaN

[3 rows x 34 columns]

In [6]:
df_train.describe()

ticket_id  violation_street_number  ...    balance_due     compliance
count  250306.000000             2.503060e+05  ...  250306.000000  159880.000000
mean   152665.543099             1.064986e+04  ...     222.449058       0.072536
std     77189.882881             3.188733e+04  ...     606.394010       0.259374
min     18645.000000             0.000000e+00  ...   -7750.000000       0.000000
25%     86549.250000             4.739000e+03  ...       0.000000       0.000000
50%    152597.500000             1.024400e+04  ...      25.000000       0.000000
75%    219888.750000             1.576000e+04  ...     305.000000       0.000000
max    366178.000000             1.415411e+07  ...   11030.000000       1.000000

[8 rows x 14 columns]

In [7]:
def stats(df):

    # This func gets the dataset and returns the number os missing values,
    # cardinality and the type of each column
    
    return pd.DataFrame({'missing':df.isna().sum(),
                          'cardinality': df.nunique(),
                          'type': df.dtypes}).sort_values(by = ['missing','cardinality'], ascending = False)

In [8]:
stats(df_train)

missing  cardinality     type
violation_zip_code           250306            0  float64
grafitti_status              250305            1   object
non_us_str_code              250303            2   object
collection_status            213409            1   object
payment_date                 209193         2307   object
compliance                    90426            2  float64
hearing_date                  12491         6222   object
mailing_address_str_number     3602        15826  float64
state                            93           59   object
violator_name                    34       119992   object
mailing_address_str_name          4        37896   object
zip_code                          1         5642   object
fine_amount                       1           43  float64
ticket_id                         0       250306    int64
ticket_issued_date                0        86979   object
violation_street_number           0        19175  float64
city                              0         5184   object
violation_street_name             0         1791   object
balance_due                       0          606  float64
payment_amount                    0          533  float64
violation_description             0          258   object
violation_code                    0          235   object
inspector_name                    0          173   object
judgment_amount                   0           57  float64
late_fee                          0           37  float64
discount_amount                   0           13  float64
compliance_detail                 0           10   object
disposition                       0            9   object
agency_name                       0            5   object
country                           0            5   object
payment_status                    0            3   object
admin_fee                         0            2  float64
state_fee                         0            2  float64
clean_up_cost                     0            1  float64

### Data Processing and Cleansing

In [9]:
# Removing rows with missing values in the target column, and in the column 
# with dates ('hearing_date')
df_train = df_train[(df_train['compliance'] == 0) | (df_train['compliance'] == 1)]
df_train = df_train[~df_train['hearing_date'].isnull()]


# Here I joined the dataframes 'address' and 'latlons' with the train and test data
address = address.set_index('address').join(latlons.set_index('address'), how='left')
df_train = df_train.set_index('ticket_id').join(address.set_index('ticket_id'))
df_test = df_test.set_index('ticket_id').join(address.set_index('ticket_id'))

Below, I removed columns that are on training data but not on the test set. This kind  of columns would lead to a Data Leakage, that is when information from outside the training dataset is used to create the model. This type of problem can destroy your Machine Learning model, since the data may have a high significance on the preditive power, but when you run the model on the test set, these data used to train won't be available.

To read more about this subject, I recommend [this article from Machine Learning Mastery](https://machinelearningmastery.com/data-leakage-machine-learning/)



In [10]:
df_train.columns[~df_train.columns.isin(df_test.columns)]

Index(['payment_amount', 'balance_due', 'payment_date', 'payment_status',
       'collection_status', 'compliance_detail', 'compliance'],
      dtype='object')

In [11]:
train_remove_list = [
        'balance_due',
        'collection_status',
        'compliance_detail',
        'payment_amount',
        'payment_date',
        'payment_status']

df_train.drop(train_remove_list, axis=1, inplace=True)

In [12]:
# Removing some string columns and redundant data
# The criteria to remove the columns was the number of missing values, if the cardinality was too high
# and if the columns had just one value, that represents a multicollinearity.

string_remove_list = ['violation_zip_code', 'grafitti_status', 'non_us_str_code', 'violator_name',
                      'mailing_address_str_name','ticket_issued_date', 'violation_street_number',
                      'hearing_date','zip_code','city', 'violation_street_name', 'violation_description',
                      'violation_code', 'inspector_name', 'admin_fee', 'state_fee', 'clean_up_cost', 'mailing_address_str_number']

df_train.drop(string_remove_list, axis=1, inplace=True)
df_test.drop(string_remove_list, axis=1, inplace=True)


In [13]:
stats(df_train)

missing  cardinality     type
state                 84           59   object
lon                    2        66767  float64
lat                    2        61497  float64
judgment_amount        0           57  float64
fine_amount            0           40  float64
late_fee               0           37  float64
discount_amount        0           12  float64
agency_name            0            5   object
country                0            5   object
disposition            0            4   object
compliance             0            2  float64

In [14]:
# Filling Missing Values in Latitude and Longitude columns by last valid observations
df_train.state.fillna(method='pad', inplace=True)
df_train.lat.fillna(method='pad', inplace=True)
df_train.lon.fillna(method='pad', inplace=True)


df_test.state.fillna(method='pad', inplace=True)
df_test.lat.fillna(method='pad', inplace=True)
df_test.lon.fillna(method='pad', inplace=True)

In [15]:
# Dividing training data in target and features columns
y_train = df_train.compliance
train = df_train.drop('compliance', axis = 1)

# Converting categorical data in numerical with the get_dummies function
train_data = pd.get_dummies(train)
test_data = pd.get_dummies(df_test)
train_data, test_data = train_data.align(test_data, join='left', axis=1)

Because of the cardinality of each dataframe, the get_dummies function created different numbers os dummies for each one. So, to compensate these 'missing columns', we use the align function, that put the Train and Test data with the same number of columns

In [16]:
test_data.fillna(0, inplace = True)

In [17]:
print('Number of columns on Train Data: {}'.format(train_data.shape[1]),
      '\nNumber of columns on Test Data : {}'.format(test_data.shape[1]))
train_data.head()

Number of columns on Train Data: 79 
Number of columns on Test Data : 79


fine_amount  ...  disposition_Responsible by Determination
ticket_id               ...                                          
22056            250.0  ...                                         0
27586            750.0  ...                                         1
22046            250.0  ...                                         0
18738            750.0  ...                                         0
18735            100.0  ...                                         0

[5 rows x 79 columns]

And that's it! Now the data is already prepared for the Machine Learning model

### Creating ML Model

In [18]:
# Here I created a function that trains a RandomForest classifier on my data 
# and returns to me the 15 most important features for the model

def feature_importances(X, y):
    
    '''
    X : Features columns
    y : Target column
    
    '''
    
    # feature extraction
    model = RandomForestClassifier(n_estimators=10)
    model.fit(X, y)
    RandomForestClassifier(bootstrap=True, class_weight=None,
                           criterion='gini', max_depth=None, max_features='auto',
                           max_leaf_nodes=None, n_estimators=10, random_state=None,
                           verbose=0, warm_start=False)

    feature_importances = pd.DataFrame(model.feature_importances_,
                                       index = X.columns,
                                       columns=['importance']).sort_values('importance', ascending=False)
    return feature_importances.iloc[0:15]

In [19]:
# Build And Train Classifier Model
classifiers = [MLPClassifier(hidden_layer_sizes = [10, 10],alpha=0.01,random_state = 0, solver='lbfgs', verbose=0),
               AdaBoostClassifier(random_state = 0),
               RandomForestClassifier(random_state = 0)
              ]

def test_classifiers(classifiers, X, y):
    
    # This func gets a list of classifiers, train it, and return the roc-auc, recall and f1 score
    # of each one. This way, I'll be able to know with witch algorithm I'll proceed with my model
    
    """
    classifiers: List of classifiers you want to train
    X          : Features columns
    y          : Target column
    
    """

    for clf in classifiers:
        clf.fit(X, y)
        name = clf.__class__.__name__

        print('='*30)
        print(name)

        print('****Result****')
        roc = cross_val_score(clf, X, y, cv = 3, scoring = 'roc_auc').mean()
        recall = cross_val_score(clf, X, y, cv = 3, scoring = 'recall').mean()
        f1 = cross_val_score(clf, X, y, cv = 3, scoring = 'f1').mean()

        print("Roc Auc Score: {}".format(roc),
              "\n Recall Score: {}".format(recall),
              "\n F1 Score: {}".format(f1))

In [ ]:
test_classifiers(classifiers, train_data, y_train)

MLPClassifier
****Result****
Roc Auc Score: 0.6539898873747864 
 Recall Score: 0.682792386454186 
 F1 Score: 0.22710659696385896
AdaBoostClassifier
****Result****
Roc Auc Score: 0.7853489163443702 
 Recall Score: 0.20320047897450236 
 F1 Score: 0.303624371771659
RandomForestClassifier
****Result****
Roc Auc Score: 0.747945631463684 
 Recall Score: 0.2622515796126376 
 F1 Score: 0.3388838511400891


Ok, here we can verify two things, one is that the models that better predict were the ones that uses ensemble methods. And the second thing is that the model returned a good roc-auc score, but a bad recall and f1 score, and generally, when it happens, is because our data is imbalanced. So, the model has a good roc-auc score, because most part of data belongs to one class, so even if the model predict all rows with just this class, we will still have a high roc-auc, since we'll have a large number of TP  

To solve this issue, I'll use the package [imblearn](https://machinelearningmastery.com/smote-oversampling-for-imbalanced-classification/). To balance the data 

#### Balancing the Dataset

In [20]:
# And, as we can verify, most part of the data belongs to the class 
# that won't pay the fines on time
y_train.value_counts()

0.0    148222
1.0     11431
Name: compliance, dtype: int64

In [21]:
oversample = SMOTE()
X_sampled, y_sampled = oversample.fit_resample(train_data, y_train)

In [22]:
pd.Series(y_sampled).value_counts()

1.0    148222
0.0    148222
dtype: int64

And, that's it. Now the classes are balanced and we can already train the model!

---

Since we could see that the RandomForest got a better performance, I'll proceed with it

In [28]:
# Dividing data in train and test set
Xtrain, Xval, ytrain, yval = train_test_split(X_sampled, y_sampled)

In [29]:
# Creating model and using the cross validation with different metrics
# to evaluate it

clf = RandomForestClassifier(random_state = 0)
clf.fit(Xtrain, ytrain)

y_pred = clf.predict(Xval)

roc = roc_auc_score(yval, y_pred)
recall = recall_score(yval, y_pred)
f1 = f1_score(yval, y_pred)

    
print("Roc Auc Score: {}".format(roc),
      "\n Recall Score: {}".format(recall),
      "\n F1 Score: {}".format(f1))

Roc Auc Score: 0.8857070534230446 
 Recall Score: 0.8792885055922383 
 F1 Score: 0.8850969168373507


As we can see, our model had a great improvement. The F1 Score was 0.34 and now it is 0.86, and the same for Recall Score.

In [30]:
# And since the model generalized very well, I'll train it using all the available data
clf.fit(X_sampled, y_sampled)

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=0, verbose=0,
                       warm_start=False)


And even though the model already has a great score, I'll try to improve it a little more using Hyperparameter-Tuning. But first, I'll use the function I created to see the 15 more imortant features in dataframe

In [31]:
Xtrain = pd.DataFrame(Xtrain)
Xtrain.columns = train_data.columns
feature_importances(Xtrain, ytrain)

importance
lon                                                   0.340133
lat                                                   0.318402
late_fee                                              0.135160
disposition_Responsible by Default                    0.060480
disposition_Responsible by Admission                  0.029287
judgment_amount                                       0.029042
disposition_Responsible by Determination              0.019932
fine_amount                                           0.011708
state_MI                                              0.011094
agency_name_Buildings, Safety Engineering & Env...    0.007422
discount_amount                                       0.005426
agency_name_Department of Public Works                0.003642
state_CA                                              0.002501
state_IL                                              0.002073
agency_name_Health Department                         0.001983

Ok, I did it, because maybe would be a good idea to do a feature engineering to better my features. But now, I'll proceed with the hyperparameter tuning:

In [32]:
def train_model(params):
    
    n_estimators = params[0]
    min_samples_split = params[1]
    
    print(params, '\n')
    
    clf = RandomForestClassifier(n_estimators = n_estimators, min_samples_split = min_samples_split, random_state = 0)
    clf.fit(X_sampled, y_sampled)
    
    #pred = clf.predict_proba(Xval)[:,1]
    
    return -cross_val_score(clf, X_sampled, y_sampled, cv = 2, scoring = 'recall').mean()



space = [(150, 1200),        # n_estimators
         (2, 100)]           # min_samples_split

In [ ]:
result = gp_minimize(train_model, space, random_state = 1, verbose = 1, n_calls = 10, n_random_starts = 2)

Iteration No: 1 started. Evaluating function at random point.
[1197, 93] 

Iteration No: 1 ended. Evaluation done at random point.
Time taken: 867.7314
Function value obtained: -0.7849
Current minimum: -0.7849
Iteration No: 2 started. Evaluating function at random point.
[285, 100] 

Iteration No: 2 ended. Evaluation done at random point.
Time taken: 217.2221
Function value obtained: -0.7836
Current minimum: -0.7849
Iteration No: 3 started. Searching for the next optimal point.
[169, 2] 

Iteration No: 3 ended. Search finished for the next optimal point.
Time taken: 151.1331
Function value obtained: -0.8747
Current minimum: -0.8747
Iteration No: 4 started. Searching for the next optimal point.
[1200, 2] 

Iteration No: 4 ended. Search finished for the next optimal point.
Time taken: 1024.9138
Function value obtained: -0.8740
Current minimum: -0.8747
Iteration No: 5 started. Searching for the next optimal point.
[150, 2] 

Iteration No: 5 ended. Search finished for the next optimal poin

In [ ]:
result.x

[153, 2]

Well, after few hours -and tuning different parameters- I could see that the standard parameters have already done an excellent job and it would be very computationally expensive to improve the model with hyperparameter-tuning. But I will leave this part on the notebook anyway, because with other models that I tested, the tuning helped a lot, besides being much faster than with RandomForest

### Reporting Findings

In [33]:
# Training again the model with the parameters I found
clf = RandomForestClassifier(n_estimators=153, min_samples_split=2,random_state=0)

clf.fit(X_sampled, y_sampled)

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=153,
                       n_jobs=None, oob_score=False, random_state=0, verbose=0,
                       warm_start=False)

In [34]:
# Creating a dataframe with lat, lon and ticket data from the testset

report_df = pd.DataFrame(columns = ({'lat','lon','ticket_id','judgment_amount'}))

report_df.set_index('ticket_id', inplace = True)

report_df.lat = test_data.lat
report_df.lon = test_data.lon
report_df.judgment_amount = test_data.judgment_amount
report_df.index = test_data.index

In [35]:
# Making predictions on the test and getting the probability 
report_df['compliance'] = clf.predict_proba(test_data)[:,1]

In [36]:
report_df

judgment_amount        lon        lat  compliance
ticket_id                                                   
284932               250.0 -82.986642  42.407581    0.405229
285362              1130.0 -83.238259  42.426239    0.006536
285361               140.0 -83.238259  42.426239    0.045752
285338               250.0 -83.122426  42.309661    0.078431
285346               140.0 -83.121116  42.308830    0.032680
...                    ...        ...        ...         ...
376496              1130.0 -83.140869  42.376675    0.000000
376497              1130.0 -83.140869  42.376675    0.000000
376499               140.0 -82.992015  42.409430    0.294118
376500               140.0 -82.991747  42.409525    0.274510
369851                80.0 -83.120740  42.349152    0.993464

[61001 rows x 4 columns]

In [37]:
# Here I classify the probabilities of compliance in 3 groups:

# 0 -> Probably won't pay the fines on time
# 1 -> Some probability of not paying on time
# 2 -> Probably will pay on time

risk = []
risk_char = []

for x in report_df.compliance:
  if x <= 0.4:
    risk.append(0)
    risk_char.append('High')
  elif x > 0.4 and x < 0.7:
    risk.append(1)
    risk_char.append('Medium')
  else:
    risk.append(2)  
    risk_char.append('Low')  

In [38]:
report_df['risk'] = risk
report_df['risk_char'] = risk_char
report_df.tail()

judgment_amount        lon        lat  compliance  risk risk_char
ticket_id                                                                   
376496              1130.0 -83.140869  42.376675    0.000000     0      High
376497              1130.0 -83.140869  42.376675    0.000000     0      High
376499               140.0 -82.992015  42.409430    0.294118     0      High
376500               140.0 -82.991747  42.409525    0.274510     0      High
369851                80.0 -83.120740  42.349152    0.993464     2       Low

In [39]:
report_df.risk_char.value_counts().sort_index()

High      44366
Low        8925
Medium     7710
Name: risk_char, dtype: int64

As we can see, most occurrences have a great risk of not paying the fines. Let's see how much this represents in loss of money for non-payment

In [40]:
print('Total Fines and Fees that probably would not be paid: ${}'.format(round(report_df['judgment_amount'][report_df['risk'] == 0].sum(), 2)))

Total Fines and Fees that probably would not be paid: $17411873.4


That is, if all these people do not actually pay, the loss will be $ 17,309,031.30


But these people are the ones who have a high chance of not paying, if we join with people who have moderate chances, then the loss will increase even more:

In [41]:
print('Total Fines and Fees that probably would not be paid: ${}'.format(round(report_df['judgment_amount'][report_df['risk'] != 2].sum(), 2)))

Total Fines and Fees that probably would not be paid: $19474714.3


Then, the loss may increase further, to around $ 19,455,675.20

These are the main descriptions of violations by those who are unlikely to pay fines on time:

In [42]:
test_raw = pd.read_csv('/content/drive/My Drive/test.csv', encoding = "ISO-8859-1")
test_raw.set_index('ticket_id', inplace = True)

In [43]:
test_raw['violation_description'][report_df['risk'] == 0].value_counts()[:10]

Excessive weeds or plant growth one- or two-family dwelling or commercial Building                                                         11678
Allowing bulk solid waste to lie or accumulate on or about the premises                                                                    11562
Failure of owner to obtain certificate of compliance                                                                                        6591
Violation of time limit for approved containers to remain at curbside - early or late                                                       1874
Failure of owner to remove graffiti or maintain or restore property free of graffiti.                                                       1456
Failure to obtain certificate of registration for rental property                                                                           1294
Inoperable motor vehicle(s) one- or two-family dwelling or commercial building                                                    

Here, I got the name, address, and postal code of those who are unlikely to pay the fines. Thus, actions can be taken to better convert the chance of payment

In [44]:
cols = ['violator_name', 'judgment_amount', 'violation_street_number', 'violation_street_name',
        'zip_code', 'city']

test_raw[cols][report_df['risk'] == 0]

violator_name  ...         city
ticket_id                                                   ...             
285362                                     WHIGHAM, THELMA  ...      DETROIT
285361                                     WHIGHAM, THELMA  ...      DETROIT
285338                                  HARABEDIEN, POPKIN  ...    WOODHAVEN
285346                                    CORBELL, STANLEY  ...      LIVONIA
285530                   INTERSTATE INVESTMENT GROUP LL, .  ...      GILBERT
...                                                    ...  ...          ...
376483     NPML Mortgage Acquistion LLC c/o Home Servicing  ...  Baton Rouge
376496                                       THE AIC GROUP  ...   Southfield
376497                                       THE AIC GROUP  ...   Southfield
376499                               BARLOW, CHRISTOPHER D  ...      DETROIT
376500                                     WILLIAMS, JASON  ...      DETROIT

[44366 rows x 6 columns]

And finally, I used the Folium package to create a map to show some occurrences of the test data with their locations, fine amount and risk of not paying

In [48]:
import folium

loc = [report_df['lat'].iloc[0]-0.03,report_df['lon'].iloc[0]-0.1]

m = folium.Map(location=loc, zoom_start=12)

colors = ['orange', 'seagreen', 'crimson']

for lat, lon, comp, ris, risc, amount in zip(report_df['lat'].head(6000), report_df['lon'].head(6000), report_df['compliance'].head(6000), report_df['risk_char'].head(6000), report_df['risk'].head(6000), report_df['judgment_amount'].head(6000)):

  label = folium.Popup(str(ris) +' Risk' + '\n Percentage:' + str(round(1 - comp, 2)) + '\n Amount: $' + str(amount))

  folium.CircleMarker(
      [lat,lon],
      radius = amount / 120,
      popup = label,
      color = colors[risc-1],
      fill = True, 
      fill_color = colors[risc-1],
      fill_opacity = 0.6,
      parse_html = False).add_to(m)

plt.tight_layout()
plt.savefig('output.png', dpi=300)

m

<Figure size 432x288 with 0 Axes>

### Conclusions

Well, to conclude and summarize this project, I believe that the model did a great job forecasting possible people who wouldn't pay on time, so with the dataframe I made available above the map, the name, address, and postal code of these residents could be taken and then the city could charge them in a different way or carry out payment promotions or things like that, probably an A/B test would say the best option. One thing is for sure, the city would certainly be able to receive a few million more if it took good strategies to approach these people and managed to convert the payment of fines.